In [1]:
import os
import json
import numpy as np
import pandas as pd
import altair as alt

In [2]:
__author__ = 'Aleksandar Anžel'
__copyright__ = ''
__credits__ = ['Aleksandar Anžel']
__license__ = 'GNU General Public License v3.0'
__version__ = '1.0'
__maintainer__ = 'Aleksandar Anžel'
__email__ = 'aleksandar.anzel@uni-marburg.de'
__status__ = 'Dev'

In [3]:
# Uncomment if you are using dark jupyter lab/notebook theme
alt.renderers.set_embed_options(theme='dark')
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

# 0. Define paths

In [4]:
path_root_data = os.path.join('..', 'Data')
path_cmangoes_vis_data = os.path.join(
    path_root_data, 'Visualization_data', 'data', 'multiple_datasets', 'vis',
    'mds_1_Overview')
path_peptidereactor_vis_data = os.path.join(
    path_root_data, 'Visualization_data', 'peptidereactor_vis_data')

path_peptidereactor_vega_lite_spec = os.path.join(
    path_cmangoes_vis_data, 'mds_1_Overview.json')

path_cmangoes_source_data = os.path.join(
    path_cmangoes_vis_data, 'hm_source_data.json')
path_cmangoes_imb_data = os.path.join(
    path_cmangoes_vis_data, 'hm_imb_data.json')
path_cmangoes_bio_data = os.path.join(
    path_cmangoes_vis_data, 'hm_bio_data.json')

path_peptidereactor_imb_data = os.path.join(
    path_peptidereactor_vis_data, 'hm_imb_data.json')
path_peptidereactor_bio_data = os.path.join(
    path_peptidereactor_vis_data, 'hm_bio_data.json')

path_cmangoes_performance_data = os.path.join(
    path_root_data, 'Performance_experiments', 'results.csv')

list_of_datasets = [
    'ace_vaxinpad',
    'acp_anticp',
    'acp_iacp',
    'acp_mlacp',
    'afp_amppred',
    'afp_antifp',
    'aip_aippred',
    'aip_antiinflam',
    'amp_antibp',
    'amp_antibp2',
    'amp_csamp',
    'amp_fernandes',
    'amp_gonzales',
    'amp_iamp2l',
    'amp_modlamp',
    'atb_antitbp',
    'atb_iantitb',
    'avp_amppred',
    'avp_avppred',
    'bce_ibce',
    'cpp_cellppd',
    'cpp_cellppdmod',
    'cpp_cppredfl',
    'cpp_kelmcpp',
    'cpp_mixed',
    'cpp_mlcpp',
    'cpp_mlcppue',
    'cpp_sanders',
    'hem_hemopi'
]

# 1. Import data

In [5]:
df_cmangoes_source_data = pd.read_json(path_cmangoes_source_data)
df_cmangoes_imb_data = pd.read_json(path_cmangoes_imb_data)
df_cmangoes_bio_data = pd.read_json(path_cmangoes_bio_data)

df_peptidereactor_imb_data = pd.read_json(path_peptidereactor_imb_data)
df_peptidereactor_bio_data = pd.read_json(path_peptidereactor_bio_data)

# 2. Clean the data

In [6]:
def df_fix_f1_scores_and_more(df_input):
    df_output = df_input.copy(deep=True)
    
    df_output = df_output[df_output['F1'] != 'separator']
    df_output['F1'] = pd.to_numeric(df_output['F1'])
    
    # We want to drop rows that contain 'zzz' at the end of the necoding
    # This flags were used to seperate heatmap
    df_output.drop(df_output[
        df_output['Encoding'].str.endswith('zzz')].index,
        inplace=True)
    df_output.drop(df_output[
        df_output['Dataset'].str.endswith('zzz')].index,
        inplace=True)
    
    df_output = df_output[df_output['Dataset'].isin(list_of_datasets)]
    
    return df_output

def df_clean_cmangoes_data(df_input):
    df_output = df_input.copy(deep=True)
    df_output = df_fix_f1_scores_and_more(df_output)
    
    df_output.drop(
        df_output[df_output['Encoding'].str.startswith('str')].index,
        inplace=True)
    
    df_output['Encoding_max'] = df_output[
        'Encoding_max'].str.replace('_levels_1_and_2_encoding','')
    df_output['Encoding_max'] = df_output[
        'Encoding_max'].str.replace('seq','CMANGOES_seq_')
    
    list_tmp = []
    for string_encoding in df_output['Encoding_max']:
        string_tmp = 'param_' + '_'.join(
            [string_chunk[:3]
             for string_chunk in string_encoding.split('_')[2:]])
        list_tmp.append(string_tmp)
    
    df_output['Encoding'] = list_tmp
    
    return df_output.reset_index(drop=True)
    

In [7]:
df_cmangoes_imb_data

Dataset Encoding                                    Encoding_max  \
0    amp_gonzales   seqdis  seqdiscretized_shifted_levels_1_and_2_encoding   
1    amp_gonzales   strdis  strdiscretized_shifted_levels_1_and_2_encoding   
2    amp_gonzales   strbin       strbinary_shifted_levels_1_and_2_encoding   
3    amp_gonzales   seqbin       seqbinary_shifted_levels_1_and_2_encoding   
4      amp_iamp2l   strbin       strbinary_shifted_levels_1_and_2_encoding   
..            ...      ...                                             ...   
115     cpp_mixed   seqbin       seqbinary_shifted_levels_1_and_2_encoding   
116   cpp_sanders   seqdis  seqdiscretized_shifted_levels_1_and_2_encoding   
117   cpp_sanders   strbin       strbinary_shifted_levels_1_and_2_encoding   
118   cpp_sanders   seqbin       seqbinary_shifted_levels_1_and_2_encoding   
119   cpp_sanders   strdis  strdiscretized_shifted_levels_1_and_2_encoding   

           F1            type  is_imbalanced bio_field  type_field  missing  
0    0.571429  sequence based       0.209302       amp           1    False  
1    0.571429  sequence based       0.209302       amp           1    False  
2         0.5  sequence based       0.209302       amp           1    False  
3         0.5  sequence based       0.209302       amp           1    False  
4    0.708928  sequence based       0.267661       amp           1    False  
..        ...             ...            ...       ...         ...      ...  
115  0.863636  sequence based       0.757812       cpp           1    False  
116  0.862745  sequence based       0.765517       cpp           1    False  
117  0.862745  sequence based       0.765517       cpp           1    False  
118  0.862745  sequence based       0.765517       cpp           1    False  
119  0.862745  sequence based       0.765517       cpp           1    False  

[120 rows x 9 columns]

In [8]:
df_cmangoes_source_data = df_clean_cmangoes_data(df_cmangoes_source_data)
df_cmangoes_imb_data = df_clean_cmangoes_data(df_cmangoes_imb_data)
df_cmangoes_bio_data = df_clean_cmangoes_data(df_cmangoes_bio_data)
df_peptidereactor_imb_data = df_fix_f1_scores_and_more(df_peptidereactor_imb_data)
df_peptidereactor_bio_data = df_fix_f1_scores_and_more(df_peptidereactor_bio_data)

df_cmangoes_imb_data

Dataset       Encoding                      Encoding_max        F1  \
0     amp_gonzales  param_dis_shi  CMANGOES_seq_discretized_shifted  0.571429   
1     amp_gonzales  param_bin_shi       CMANGOES_seq_binary_shifted  0.500000   
2       amp_iamp2l  param_dis_shi  CMANGOES_seq_discretized_shifted  0.716014   
3       amp_iamp2l  param_bin_shi       CMANGOES_seq_binary_shifted  0.708928   
4        acp_mlacp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.403390   
5        acp_mlacp  param_bin_shi       CMANGOES_seq_binary_shifted  0.353913   
6        cpp_mlcpp  param_bin_shi       CMANGOES_seq_binary_shifted  0.379744   
7        cpp_mlcpp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.401970   
8      aip_aippred  param_dis_shi  CMANGOES_seq_discretized_shifted  0.483782   
9      aip_aippred  param_bin_shi       CMANGOES_seq_binary_shifted  0.476557   
10        acp_iacp  param_bin_shi       CMANGOES_seq_binary_shifted  0.352941   
11        acp_iacp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.410256   
12  aip_antiinflam  param_bin_shi       CMANGOES_seq_binary_shifted  0.444450   
13  aip_antiinflam  param_dis_shi  CMANGOES_seq_discretized_shifted  0.470537   
14    ace_vaxinpad  param_dis_shi  CMANGOES_seq_discretized_shifted  0.618182   
15    ace_vaxinpad  param_bin_shi       CMANGOES_seq_binary_shifted  0.609477   
16        bce_ibce  param_bin_shi       CMANGOES_seq_binary_shifted  0.505379   
17        bce_ibce  param_dis_shi  CMANGOES_seq_discretized_shifted  0.516849   
18      hem_hemopi  param_dis_shi  CMANGOES_seq_discretized_shifted  0.696085   
19      hem_hemopi  param_bin_shi       CMANGOES_seq_binary_shifted  0.668309   
20     amp_modlamp  param_bin_shi       CMANGOES_seq_binary_shifted  0.725397   
21     amp_modlamp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.768068   
22   amp_fernandes  param_dis_shi  CMANGOES_seq_discretized_shifted  0.696939   
23   amp_fernandes  param_bin_shi       CMANGOES_seq_binary_shifted  0.694765   
24     atb_antitbp  param_bin_shi       CMANGOES_seq_binary_shifted  0.593706   
25     avp_amppred  param_dis_shi  CMANGOES_seq_discretized_shifted  0.649503   
26      acp_anticp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.715789   
27     cpp_cellppd  param_dis_shi  CMANGOES_seq_discretized_shifted  0.690515   
28    cpp_cppredfl  param_dis_shi  CMANGOES_seq_discretized_shifted  0.545455   
29       amp_csamp  param_bin_shi       CMANGOES_seq_binary_shifted  0.928571   
30     cpp_mlcppue  param_dis_shi  CMANGOES_seq_discretized_shifted  0.619381   
31     afp_amppred  param_bin_shi       CMANGOES_seq_binary_shifted  0.656542   
32     cpp_mlcppue  param_bin_shi       CMANGOES_seq_binary_shifted  0.601205   
33      acp_anticp  param_bin_shi       CMANGOES_seq_binary_shifted  0.708374   
34     atb_iantitb  param_dis_shi  CMANGOES_seq_discretized_shifted  0.613237   
35     atb_antitbp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.595999   
36       amp_csamp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.925926   
37     afp_amppred  param_dis_shi  CMANGOES_seq_discretized_shifted  0.667239   
38     cpp_cellppd  param_bin_shi       CMANGOES_seq_binary_shifted  0.679138   
39     avp_amppred  param_bin_shi       CMANGOES_seq_binary_shifted  0.638235   
40     atb_iantitb  param_bin_shi       CMANGOES_seq_binary_shifted  0.604639   
41    cpp_cppredfl  param_bin_shi       CMANGOES_seq_binary_shifted  0.564254   
42      afp_antifp  param_bin_shi       CMANGOES_seq_binary_shifted  0.536668   
43      afp_antifp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.554842   
44      amp_antibp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.695652   
45      amp_antibp  param_bin_shi       CMANGOES_seq_binary_shifted  0.670888   
46  cpp_cellppdmod  param_dis_shi  CMANGOES_seq_discretized_shifted  0.754583   
47  cpp_cellppdmod  param_bin_shi       CMANGOES_seq_binary_shifted  0.745315   
48     amp_antibp2  param_bin_shi       CM

In [9]:
df_peptidereactor_imb_data

Dataset Encoding              Encoding_max        F1  \
138   amp_gonzales   geary_              geary_nlag_9  0.750000   
139   amp_gonzales   flgc_a   flgc_aaindex_ZIMJ680104  0.888889   
140   amp_gonzales   dist_f      dist_freq_dn_5_dc_50  0.888889   
141   amp_gonzales   ngram_                ngram_s3_5  0.816667   
142   amp_gonzales   fldpc_  fldpc_aaindex_ZIMJ680104  0.888889   
...            ...      ...                       ...       ...   
2339   cpp_sanders     ctdt                      ctdt  0.872283   
2340   cpp_sanders   ksctri            ksctriad_gap_1  0.872283   
2341   cpp_sanders   flgc_a   flgc_aaindex_ZIMJ680104  0.875000   
2342   cpp_sanders   ctriad                    ctriad  0.875000   
2343   cpp_sanders      dde                       dde  0.877500   

                type  is_imbalanced bio_field  type_field  missing  
138   sequence based       0.209302       amp           1    False  
139   sequence based       0.209302       amp           1    False  
140   sequence based       0.209302       amp           1    False  
141   sequence based       0.209302       amp           1    False  
142   sequence based       0.209302       amp           1    False  
...              ...            ...       ...         ...      ...  
2339  sequence based       0.765517       cpp           1    False  
2340  sequence based       0.765517       cpp           1    False  
2341  sequence based       0.765517       cpp           1    False  
2342  sequence based       0.765517       cpp           1    False  
2343  sequence based       0.765517       cpp           1    False  

[1305 rows x 9 columns]

In [10]:
df_combined_imb_data = pd.concat(
    [df_cmangoes_imb_data, df_peptidereactor_imb_data], ignore_index=True)
df_combined_bio_data = pd.concat(
    [df_cmangoes_bio_data, df_peptidereactor_bio_data], ignore_index=True)

df_combined_imb_data

Dataset       Encoding                      Encoding_max        F1  \
0     amp_gonzales  param_dis_shi  CMANGOES_seq_discretized_shifted  0.571429   
1     amp_gonzales  param_bin_shi       CMANGOES_seq_binary_shifted  0.500000   
2       amp_iamp2l  param_dis_shi  CMANGOES_seq_discretized_shifted  0.716014   
3       amp_iamp2l  param_bin_shi       CMANGOES_seq_binary_shifted  0.708928   
4        acp_mlacp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.403390   
...            ...            ...                               ...       ...   
1358   cpp_sanders           ctdt                              ctdt  0.872283   
1359   cpp_sanders         ksctri                    ksctriad_gap_1  0.872283   
1360   cpp_sanders         flgc_a           flgc_aaindex_ZIMJ680104  0.875000   
1361   cpp_sanders         ctriad                            ctriad  0.875000   
1362   cpp_sanders            dde                               dde  0.877500   

                type  is_imbalanced bio_field  type_field  missing  
0     sequence based       0.209302       amp           1    False  
1     sequence based       0.209302       amp           1    False  
2     sequence based       0.267661       amp           1    False  
3     sequence based       0.267661       amp           1    False  
4     sequence based       0.319658       acp           1    False  
...              ...            ...       ...         ...      ...  
1358  sequence based       0.765517       cpp           1    False  
1359  sequence based       0.765517       cpp           1    False  
1360  sequence based       0.765517       cpp           1    False  
1361  sequence based       0.765517       cpp           1    False  
1362  sequence based       0.765517       cpp           1    False  

[1363 rows x 9 columns]

In [11]:
df_combined_imb_data

Dataset       Encoding                      Encoding_max        F1  \
0     amp_gonzales  param_dis_shi  CMANGOES_seq_discretized_shifted  0.571429   
1     amp_gonzales  param_bin_shi       CMANGOES_seq_binary_shifted  0.500000   
2       amp_iamp2l  param_dis_shi  CMANGOES_seq_discretized_shifted  0.716014   
3       amp_iamp2l  param_bin_shi       CMANGOES_seq_binary_shifted  0.708928   
4        acp_mlacp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.403390   
...            ...            ...                               ...       ...   
1358   cpp_sanders           ctdt                              ctdt  0.872283   
1359   cpp_sanders         ksctri                    ksctriad_gap_1  0.872283   
1360   cpp_sanders         flgc_a           flgc_aaindex_ZIMJ680104  0.875000   
1361   cpp_sanders         ctriad                            ctriad  0.875000   
1362   cpp_sanders            dde                               dde  0.877500   

                type  is_imbalanced bio_field  type_field  missing  
0     sequence based       0.209302       amp           1    False  
1     sequence based       0.209302       amp           1    False  
2     sequence based       0.267661       amp           1    False  
3     sequence based       0.267661       amp           1    False  
4     sequence based       0.319658       acp           1    False  
...              ...            ...       ...         ...      ...  
1358  sequence based       0.765517       cpp           1    False  
1359  sequence based       0.765517       cpp           1    False  
1360  sequence based       0.765517       cpp           1    False  
1361  sequence based       0.765517       cpp           1    False  
1362  sequence based       0.765517       cpp           1    False  

[1363 rows x 9 columns]

In [12]:
# Add one more column to flag missing values
df_combined_imb_data['Value'] = [
    'NaN' if i is True else 'notNaN'
    for i in df_combined_imb_data['F1'].isnull().tolist()]
df_combined_bio_data['Value'] = [
    'NaN' if i is True else 'notNaN'
    for i in df_combined_bio_data['F1'].isnull().tolist()]

In [13]:
df_combined_imb_data

Dataset       Encoding                      Encoding_max        F1  \
0     amp_gonzales  param_dis_shi  CMANGOES_seq_discretized_shifted  0.571429   
1     amp_gonzales  param_bin_shi       CMANGOES_seq_binary_shifted  0.500000   
2       amp_iamp2l  param_dis_shi  CMANGOES_seq_discretized_shifted  0.716014   
3       amp_iamp2l  param_bin_shi       CMANGOES_seq_binary_shifted  0.708928   
4        acp_mlacp  param_dis_shi  CMANGOES_seq_discretized_shifted  0.403390   
...            ...            ...                               ...       ...   
1358   cpp_sanders           ctdt                              ctdt  0.872283   
1359   cpp_sanders         ksctri                    ksctriad_gap_1  0.872283   
1360   cpp_sanders         flgc_a           flgc_aaindex_ZIMJ680104  0.875000   
1361   cpp_sanders         ctriad                            ctriad  0.875000   
1362   cpp_sanders            dde                               dde  0.877500   

                type  is_imbalanced bio_field  type_field  missing   Value  
0     sequence based       0.209302       amp           1    False  notNaN  
1     sequence based       0.209302       amp           1    False  notNaN  
2     sequence based       0.267661       amp           1    False  notNaN  
3     sequence based       0.267661       amp           1    False  notNaN  
4     sequence based       0.319658       acp           1    False  notNaN  
...              ...            ...       ...         ...      ...     ...  
1358  sequence based       0.765517       cpp           1    False  notNaN  
1359  sequence based       0.765517       cpp           1    False  notNaN  
1360  sequence based       0.765517       cpp           1    False  notNaN  
1361  sequence based       0.765517       cpp           1    False  notNaN  
1362  sequence based       0.765517       cpp           1    False  notNaN  

[1363 rows x 10 columns]

# 3. Visualize
## 3.1. CMANGOES results

In [14]:
def chart_visualize(df_input, string_title, flag_cmangoes_style):
    
    if flag_cmangoes_style:
        scale_general = alt.Scale(scheme='greys', domain=[0, 1])
        scale_na_values = alt.Scale(domain=['NaN'], range=['#CD7DA9'])
    else:
        scale_general = alt.Scale(range=["#a6bddb", "#023858"])
        scale_na_values = alt.Scale(domain=['NaN'], range=['#a6611a'])
    
    
    chart_non_null = alt.Chart(
        df_input, title=string_title + " multi-dataset results"
    ).mark_rect().encode(
        x=alt.X('Encoding', type='nominal', axis=alt.Axis(labelAngle=-45)),
        y=alt.Y('Dataset', type='nominal',
                scale=alt.Scale(domain=list_of_datasets)),
        color=alt.Color('F1', type='quantitative', scale=scale_general),
        tooltip=['Dataset', 'Encoding_max', 'F1', 'is_imbalanced', 'bio_field']
    )
    
    chart_null = alt.Chart(
        df_input, title=string_title + " multi-dataset results"
    ).mark_rect().encode(
        x=alt.X('Encoding', type='nominal', axis=alt.Axis(labelAngle=-45)),
        y=alt.Y('Dataset', type='nominal',
                scale=alt.Scale(domain=list_of_datasets)),
        color=alt.Color('Value', type='nominal', scale=scale_na_values),
        tooltip=['Dataset', 'Encoding_max', 'F1', 'is_imbalanced', 'bio_field']
    )
    
    chart_result = chart_non_null + chart_null
    
    return chart_result


def replicate_visualizations(flag_visualization_style):
    chart_cmangoes_source_result = chart_visualize(
        df_cmangoes_source_data, 'CMANGOES source', flag_visualization_style)
    chart_peptidereactor_imb_result = chart_visualize(
        df_peptidereactor_imb_data, 'Peptidereactor imb',
        flag_visualization_style)
    chart_peptidereactor_bio_result = chart_visualize(
        df_peptidereactor_bio_data, 'Peptidereactor bio',
        flag_visualization_style)
    chart_combined_imb_result = chart_visualize(
        df_combined_imb_data, 'Combined imb', flag_visualization_style)
    chart_combined_bio_result = chart_visualize(
        df_combined_bio_data, 'Combined bio', flag_visualization_style)

    chart_result = chart_cmangoes_source_result &\
                   chart_peptidereactor_imb_result &\
                   chart_peptidereactor_bio_result &\
                   chart_combined_imb_result &\
                   chart_combined_bio_result

    return chart_result


## 3.1. Peptidereactor-styled results

In [15]:
flag_cmangoes_style = True
replicate_visualizations(not flag_cmangoes_style)

alt.VConcatChart(...)

## 3.2. Our own visualizations

In [16]:
replicate_visualizations(flag_cmangoes_style)

alt.VConcatChart(...)

## 3.3 Further analysis of encodings

In [17]:
def chart_filter_and_visualize(df_input, string_column, float_value):
    scale_upper = alt.Scale(scheme='greys', domain=[0, 1])
    scale_lower = alt.Scale(domain=['Cut-off'], range=['white']) # #9ecae1
    scale_na_values = alt.Scale(domain=['NaN'], range=['#CD7DA9'])
    string_title_addon = ' combined multi-dataset results.' +\
        ' Cells in white represent the cut-off values'
    
    if string_column == 'F1':
        float_new_value = df_input[string_column].quantile(q=float_value)
        string_title = string_column + ' > ' + str(int(float_value*100)) +\
        ' percent'
        field_upper = alt.FieldGTPredicate(field=string_column,
                                           gt=float_new_value)
        field_lower = alt.FieldLTEPredicate(field=string_column,
                                            lte=float_new_value)
    elif string_column == 'is_imbalanced':
        float_new_value = float_value
        string_title = string_column + ' == ' + str(float_value)
        field_upper =  alt.FieldEqualPredicate(field=string_column,
                                               equal=float_new_value)
        field_lower = {'not': alt.FieldEqualPredicate(field=string_column,
                                                      equal=float_new_value)}
    else:
        print('Not valid column name')
        return None
    
    chart_base = alt.Chart(
        df_input, title=string_title + string_title_addon
    ).mark_rect().encode(
        alt.X('Encoding', type='nominal', axis=alt.Axis(labelAngle=-45)),
        alt.Y('Dataset', type='nominal',
                scale=alt.Scale(domain=list_of_datasets)),
        tooltip=['Dataset', 'Encoding_max', 'F1', 'is_imbalanced', 'bio_field']
    )
    
    chart_upper = chart_base.encode(
        alt.Color('F1', type='quantitative', scale=scale_upper),
    ).transform_filter(field_upper)
    
    chart_lower = chart_base.encode(
        alt.Color('F1', type='quantitative', scale=scale_lower, legend=None),
        alt.Opacity('F1', type='quantitative', scale=alt.Scale(
            domain=['Cut-off'], range=[0.2]))
    ).transform_filter(field_lower)
    
    chart_null = chart_base.encode(
        alt.Color('Value', type='nominal', scale=scale_na_values),
    )

    chart_result = alt.layer(
        chart_upper, chart_lower, chart_null).resolve_scale(
        color='independent')
    
    return chart_result


def chart_f1_correlation(df_input):
    
    df_filtered = df_input[['Encoding', 'Dataset', 'F1']]
    df_pivoted = pd.pivot(df_filtered, index='Dataset', columns='Encoding',
                          values='F1')
    df_pivoted.columns.rename('', inplace=True)
    df_pivoted.index.rename('Encoding', inplace=True)
    df_corr = df_pivoted.corr(method='pearson').reset_index()
    df_corr.rename(columns={'': 'Encoding'}, inplace=True)
    df_corr = df_corr.melt('Encoding')
    
    df_corr.columns = ['var_1', 'var_2', 'correlation']
    
    # Create correlation matrix chart
    chart_corr = alt.Chart(df_corr).mark_rect().encode(
        alt.X ('var_1', title=None, axis=alt.Axis(labelAngle=-30,
                                                  title='Encoding')),
        alt.Y ('var_2', title=None, axis=alt.Axis(title='Encoding')),
        alt.Color('correlation', scale=alt.Scale(
            domain=[-1, 1], scheme='redblue', reverse=True)),
        alt.Tooltip(['var_1', 'var_2'])
    ).properties(
        width=alt.Step(40),
        height=alt.Step(40)
    )
    
    # Create text values for each colored element on top of existing chart
    chart_text = chart_corr.mark_text(size=12).encode(
        alt.Text('correlation', format=".2f"),
        color=alt.condition("abs(datum.correlation) > 0.6", alt.value('white'),
                            alt.value('black'))
    )
    
    chart_result = alt.layer(chart_corr, chart_text)
    
    return chart_result.transform_filter("datum.var_1 < datum.var_2")


In [18]:
chart_f1_correlation(df_combined_imb_data)

alt.LayerChart(...)

In [19]:
chart_filter_and_visualize(df_combined_imb_data, 'F1', 0.75)

alt.LayerChart(...)

In [20]:
chart_filter_and_visualize(df_combined_imb_data, 'is_imbalanced', 0.5)

alt.LayerChart(...)

## 3.4 Performance analysis

In [21]:
df_performance_results = pd.read_csv(path_cmangoes_performance_data)
df_performance_results

Dataset                                          Encodings  \
0    ace_vaxinpad       ace_vaxinpad_binary_centered_levels_1_and_2_   
1    ace_vaxinpad        ace_vaxinpad_binary_shifted_levels_1_and_2_   
2    ace_vaxinpad  ace_vaxinpad_discretized_centered_levels_1_and_2_   
3    ace_vaxinpad   ace_vaxinpad_discretized_shifted_levels_1_and_2_   
4      acp_anticp         acp_anticp_binary_centered_levels_1_and_2_   
..            ...                                                ...   
111   cpp_sanders    cpp_sanders_discretized_shifted_levels_1_and_2_   
112    hem_hemopi         hem_hemopi_binary_centered_levels_1_and_2_   
113    hem_hemopi          hem_hemopi_binary_shifted_levels_1_and_2_   
114    hem_hemopi    hem_hemopi_discretized_centered_levels_1_and_2_   
115    hem_hemopi     hem_hemopi_discretized_shifted_levels_1_and_2_   

         Run_3      Run_4      Run_5      Run_0      Run_1      Run_2  
0    21.531495  21.766941  21.754083  20.885754  20.847980  21.150071  
1    21.840645  22.009670  21.966192  21.003920  20.989860  21.287949  
2    30.321533  30.385960  30.376384  28.740059  28.816950  29.282086  
3    30.305075  30.396818  30.511680  28.779231  28.861472  29.302293  
4    31.775193  31.631264  31.671900  30.269795  30.303933  30.795589  
..         ...        ...        ...        ...        ...        ...  
111  10.071117  10.017213  10.013413   9.578461   9.707204   9.721294  
112  59.093313  59.090154  59.101917  57.135355  58.004068  58.125769  
113  60.432704  60.308071  60.330473  58.395762  59.240168  59.277407  
114  83.537105  83.471676  83.341212  79.766179  81.008070  81.112379  
115  83.652212  83.504252  83.470714  79.973635  81.224380  81.183970  

[116 rows x 8 columns]

In [22]:
df_performance_results_new = df_performance_results.drop(
    'Encodings', axis=1).melt('Dataset')
df_performance_results_new['TMP_LEGEND'] = len(
    df_performance_results_new['Dataset']) * ['Median']
df_performance_results_new

Dataset variable      value TMP_LEGEND
0    ace_vaxinpad    Run_3  21.531495     Median
1    ace_vaxinpad    Run_3  21.840645     Median
2    ace_vaxinpad    Run_3  30.321533     Median
3    ace_vaxinpad    Run_3  30.305075     Median
4      acp_anticp    Run_3  31.775193     Median
..            ...      ...        ...        ...
691   cpp_sanders    Run_2   9.721294     Median
692    hem_hemopi    Run_2  58.125769     Median
693    hem_hemopi    Run_2  59.277407     Median
694    hem_hemopi    Run_2  81.112379     Median
695    hem_hemopi    Run_2  81.183970     Median

[696 rows x 4 columns]

In [23]:
x_domain = alt.selection_interval(bind='scales', encodings=['x'])
chart_performance_error_bars = alt.Chart(
    df_performance_results_new).mark_errorbar(
    extent='ci', color='#afafaf').encode(
    x=alt.X('Dataset', type='nominal', axis=alt.Axis(labelAngle=-45)),
    y=alt.Y('value', type='quantitative', title='Seconds'),
    strokeWidth=alt.value(2)
).add_selection(
    x_domain
)

chart_performance_points_error = alt.Chart(
    df_performance_results_new).mark_point(filled=True, color='black').encode(
    alt.X('Dataset', type='nominal', axis=alt.Axis(
        labelAngle=-45, labels=False, ticks=False, title='')),
    alt.Y('value', type='quantitative', aggregate='median', title=''),
    alt.Tooltip(['Dataset', 'median(value)']),
    alt.Opacity('TMP_LEGEND', type='nominal', legend=alt.Legend(title='')),

).add_selection(
    x_domain
)

chart_performance_error_bars_result = alt.layer(chart_performance_error_bars,
                                               chart_performance_points_error)
chart_performance_error_bars_result

alt.LayerChart(...)

In [24]:
# Calculate dataset sizes
# os.path.getsize("/path/to/file.mp3")
df_dataset_sizes = pd.DataFrame()
df_dataset_sizes['Dataset'] = list_of_datasets
path_original_data = os.path.join(path_root_data, 'Original_datasets')

list_sizes = []

for string_one_dataset in list_of_datasets:
    path_one_dataset = os.path.join(path_original_data, string_one_dataset)
    list_sizes.append(os.path.getsize(
        os.path.join(path_one_dataset, 'classes.txt')) + os.path.getsize(
        os.path.join(path_one_dataset, 'seqs.fasta')))

df_dataset_sizes['Size_in_bytes'] = list_sizes
df_dataset_sizes


Dataset  Size_in_bytes
0     ace_vaxinpad          16346
1       acp_anticp          17075
2         acp_iacp          12788
3        acp_mlacp          23927
4      afp_amppred         131427
5       afp_antifp         197437
6      aip_aippred          34784
7   aip_antiinflam          59822
8       amp_antibp          36054
9      amp_antibp2          84034
10       amp_csamp          25260
11   amp_fernandes          18394
12    amp_gonzales           5332
13      amp_iamp2l         232273
14     amp_modlamp         143535
15     atb_antitbp          13770
16     atb_iantitb          13545
17     avp_amppred          61020
18     avp_avppred          38203
19        bce_ibce         110519
20     cpp_cellppd          49898
21  cpp_cellppdmod          42583
22    cpp_cppredfl          29888
23     cpp_kelmcpp          32567
24       cpp_mixed           3608
25       cpp_mlcpp          62404
26     cpp_mlcppue          10184
27     cpp_sanders           4280
28      hem_hemopi          43146

In [25]:
chart_size_bars = alt.Chart(
    df_dataset_sizes).mark_bar(color='gray').encode(
    alt.X('Dataset', type='nominal', axis=alt.Axis(
        labelAngle=-45, labels=False, ticks=False, title='')),
    alt.Y('Size_in_bytes', type='quantitative', title='Bytes'),
    alt.Tooltip(['Dataset', 'Size_in_bytes'])
).add_selection(
    x_domain
)

chart_size_bars

alt.Chart(...)

In [26]:
chart_imbalance_bars = alt.Chart(
    df_cmangoes_source_data).mark_bar(color='gray').encode(
    alt.X('Dataset', type='nominal', axis=alt.Axis(labelAngle=-45)),
    alt.Y('is_imbalanced', type='quantitative', title='Imbalance_ratio',
         scale=alt.Scale(domain=[0, 1])),
    alt.Tooltip(['Dataset', 'is_imbalanced'])
).add_selection(
    x_domain
)
chart_imbalance_bars


alt.Chart(...)

In [27]:
chart_final_performance_result = alt.vconcat(
    chart_performance_error_bars_result,
    chart_size_bars,
    chart_imbalance_bars
)
chart_final_performance_result

alt.VConcatChart(...)